In [1]:
import numpy as np
import pandas as pd

import warnings
warnings.filterwarnings('ignore')

In [2]:
df = pd.read_csv('/kaggle/input/extract/test.csv')
df = df[['Article','Summary']]
df

Article  \
0     Fear shakes Mexico border city after violence ...   
1     Indian-origin boy finds millions of years old ...   
2     Representative ImageA 38-year-old Indian man h...   
3     Residents get tested during their stay at a te...   
4     Israeli PM Benjamin Netanyahu flew to Saudi Ar...   
...                                                 ...   
4482  FILE - Tanks storing treated radioactive water...   
4483  Villagers clear debris caused by an earthquake...   
4484  Seif al-Islam, the son and one-time heir appar...   
4485  Thai BoysMost members of the Thai youth footba...   
4486  Karachi to award citizens who identify people ...   

                                                Summary  
0     The attacks took place in several neighborhood...  
1     Siddak Singh Jhamat, known as Sid, was using a...  
2     A 38-year-old Indian man has been charged with...  
3     China on Apr 21 reported 2,119 locally transmi...  
4     Israeli media reported Monday that Prime Minis...  
...                                                 ...  
4482  A massive earthquake and tsunami in 2011 destr...  
4483  Over 680 tourists from France, Thailand, the N...  
4484  Seif al-Islam, the son and one-time heir appar...  
4485  Most members of the Thai youth football team r...  
4486  The government of Pakistan's Sindh province ha...  

[4487 rows x 2 columns]

In [3]:
!pip install rouge -q
!pip install evaluate -q
!pip install rouge-score -q
!pip install -q textstat

In [4]:
!pip install transformers -q
!pip install sentence-transformers -q

In [5]:
import torch
import re
from transformers import AutoTokenizer, AutoModel
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd
model_name = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModel.from_pretrained(model_name)

In [6]:
from sentence_transformers import SentenceTransformer
sbert_model = SentenceTransformer('bert-base-nli-mean-tokens')

In [7]:
def cosine(u, v):
    return np.dot(u, v) / (np.linalg.norm(u) * np.linalg.norm(v))

In [8]:
article = df['Article'][0]
article

'Fear shakes Mexico border city after violence leaves 18 deadFear has invaded the Mexican border city of Reynosa after gunmen in vehicles killed 14 people, including taxi drivers, workers and a nursing student, and security forces responded with operations that left four suspects dead.While this city across the border from McAllen, Texas is used to cartel violence as a key trafficking point, the 14 victims in Saturday’s attacks appeared to be what Tamaulipas Gov. Francisco García Cabeza de Vaca called “innocent citizens” rather than members of one gang killed by a rival.Local businessman Misael Chavarria Garza said many businesses closed early Saturday after the attacks and people were very scared as helicopters flew overhead. On Sunday, he said, “the people were quiet as if nothing had happened, but with a feeling of anger because now crime has happened to innocent people.”“It’s not fair,” said taxi driver Rene Guevara, adding that among the dead were two of his fellow taxi drivers wh

In [9]:
import nltk
from nltk.tokenize import sent_tokenize

In [10]:
sentences = sent_tokenize(article)
sentences

['Fear shakes Mexico border city after violence leaves 18 deadFear has invaded the Mexican border city of Reynosa after gunmen in vehicles killed 14 people, including taxi drivers, workers and a nursing student, and security forces responded with operations that left four suspects dead.While this city across the border from McAllen, Texas is used to cartel violence as a key trafficking point, the 14 victims in Saturday’s attacks appeared to be what Tamaulipas Gov.',
 'Francisco García Cabeza de Vaca called “innocent citizens” rather than members of one gang killed by a rival.Local businessman Misael Chavarria Garza said many businesses closed early Saturday after the attacks and people were very scared as helicopters flew overhead.',
 'On Sunday, he said, “the people were quiet as if nothing had happened, but with a feeling of anger because now crime has happened to innocent people.”“It’s not fair,” said taxi driver Rene Guevara, adding that among the dead were two of his fellow taxi d

In [11]:
len(sentences)

11

In [12]:
article_embed = sbert_model.encode(article)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [13]:
len(article_embed)

768

In [14]:
sentence_embeds = []
for sent in sentences:
    embed = sbert_model.encode(sent)
    sentence_embeds.append(embed)
    
len(sentence_embeds)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

11

In [15]:
sims = []
for embed in sentence_embeds:
    sim = cosine(embed, article_embed)
    sims.append(sim)
    
len(sims)

11

In [16]:
res = pd.DataFrame()
res['Sentence'] = sentences
res['Sim Value'] = sims
res

Sentence  Sim Value
0   Fear shakes Mexico border city after violence ...   0.982563
1   Francisco García Cabeza de Vaca called “innoce...   0.795303
2   On Sunday, he said, “the people were quiet as ...   0.807429
3   Images posted on social media showed bodies in...   0.763131
4   Experts say there has been an internal struggl...   0.602479
5   Apparently, one cell from a nearby town may ha...   0.767661
6   “They stopped in front of them and started to ...   0.776007
7   He has assured Mexicans that he is fighting th...   0.622981
8   He also says he is fighting corruption to stop...   0.681011
9   “In my government, there will be no truce for ...   0.788029
10  One former governor, Tomás Yarrington, was ext...   0.596762

In [17]:
sent1 = res['Sentence'][0]
sent1

'Fear shakes Mexico border city after violence leaves 18 deadFear has invaded the Mexican border city of Reynosa after gunmen in vehicles killed 14 people, including taxi drivers, workers and a nursing student, and security forces responded with operations that left four suspects dead.While this city across the border from McAllen, Texas is used to cartel violence as a key trafficking point, the 14 victims in Saturday’s attacks appeared to be what Tamaulipas Gov.'

In [18]:
df['Summary'][0]

'The attacks took place in several neighborhoods in eastern Reynosa, according to the Tamaulipas state agency that coordinates security forces, and sparked a deployment of the military, National Guard and state police across the city. Images posted on social media showed bodies in the streets.'

In [19]:
from rouge import Rouge
rouge = Rouge()
score = rouge.get_scores(sent1, df['Summary'][0], avg = True)
RougeScore = pd.DataFrame(score).set_index([['recall','precision','f-measure']])
RougeScore

rouge-1   rouge-2   rouge-l
recall     0.315789  0.022727  0.078947
precision  0.193548  0.013699  0.048387
f-measure  0.240000  0.017094  0.060000

## My Tokinizer

In [20]:
sentences = article.split('.')
sentences = [x for x in sentences if x]
sentences

['Fear shakes Mexico border city after violence leaves 18 deadFear has invaded the Mexican border city of Reynosa after gunmen in vehicles killed 14 people, including taxi drivers, workers and a nursing student, and security forces responded with operations that left four suspects dead',
 'While this city across the border from McAllen, Texas is used to cartel violence as a key trafficking point, the 14 victims in Saturday’s attacks appeared to be what Tamaulipas Gov',
 ' Francisco García Cabeza de Vaca called “innocent citizens” rather than members of one gang killed by a rival',
 'Local businessman Misael Chavarria Garza said many businesses closed early Saturday after the attacks and people were very scared as helicopters flew overhead',
 ' On Sunday, he said, “the people were quiet as if nothing had happened, but with a feeling of anger because now crime has happened to innocent people',
 '”“It’s not fair,” said taxi driver Rene Guevara, adding that among the dead were two of his f

In [21]:
sentence_embeds = []
for sent in sentences:
    embed = sbert_model.encode(sent)
    sentence_embeds.append(embed)
    
len(sentence_embeds)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

27

In [22]:
sims = []
for embed in sentence_embeds:
    sim = cosine(embed, article_embed)
    sims.append(sim)
    
len(sims)

27

In [23]:
res = pd.DataFrame()
res['Sentence'] = sentences
res['Sim Value'] = sims
res

Sentence  Sim Value
0   Fear shakes Mexico border city after violence ...   0.916957
1   While this city across the border from McAllen...   0.855924
2    Francisco García Cabeza de Vaca called “innoc...   0.624474
3   Local businessman Misael Chavarria Garza said ...   0.677645
4    On Sunday, he said, “the people were quiet as...   0.536978
5   ”“It’s not fair,” said taxi driver Rene Guevar...   0.682906
6   The attacks took place in several neighborhood...   0.599028
7    Images posted on social media showed bodies i...   0.348252
8   Authorities say they are investigating the att...   0.408798
9   But the area’s criminal activity has long been...   0.637984
10   Experts say there has been an internal strugg...   0.600307
11   Apparently, one cell from a nearby town may h...   0.456644
12  Olga Ruiz, whose 19-year-old brother Fernando ...   0.681791
13  “They killed him in cold blood, he and two of ...   0.729528
14  “They heard the gunshots from afar and my step...   0.531874
15  ’ So he asked permission to enter a house but ...   0.431439
16   “They stopped in front of them and started to...   0.170587
17  ”On Saturday, authorities detained a person wh...   0.673381
18  Security is one of the great challenges facing...   0.388292
19   He has assured Mexicans that he is fighting t...   0.625094
20   He also says he is fighting corruption to sto...   0.586226
21                         But the violence continues   0.196765
22  “Criminal organizations must receive a clear, ...   0.606244
23   “In my government, there will be no truce for...   0.506968
24  ”But García Cabeza de Vaca himself is being in...   0.682743
25  Tamaulipas - the state where the Zetas cartel ...   0.710380
26   One former governor, Tomás Yarrington, was ex...   0.597163

In [24]:
sent1 = res['Sentence'][0]
sent1 = sent1 + res['Sentence'][13]
sent1

'Fear shakes Mexico border city after violence leaves 18 deadFear has invaded the Mexican border city of Reynosa after gunmen in vehicles killed 14 people, including taxi drivers, workers and a nursing student, and security forces responded with operations that left four suspects dead“They killed him in cold blood, he and two of his companions,” said Olga Ruiz, adding that the gunmen arrived where her brother was fixing a drain'

In [25]:
from rouge import Rouge
rouge = Rouge()
score = rouge.get_scores(sent1, df['Summary'][0], avg = True)
RougeScore = pd.DataFrame(score).set_index([['recall','precision','f-measure']])
RougeScore

rouge-1  rouge-2   rouge-l
recall     0.210526      0.0  0.105263
precision  0.137931      0.0  0.068966
f-measure  0.166667      0.0  0.083333

## Testing

In [26]:
article_embed 

array([ 2.09677488e-01,  4.56588686e-01, -2.08456397e-01,  1.11587197e-01,
        2.96344217e-02,  1.83288120e-02,  7.56460786e-01,  3.18880796e-01,
        1.91578418e-01,  4.20202553e-01,  3.72932434e-01,  5.52363470e-02,
        6.30580038e-02,  5.72204769e-01, -9.63303089e-01,  3.68067920e-01,
       -4.66601729e-01,  1.77772388e-01, -2.35283524e-01,  1.29180282e-01,
        4.74667661e-02, -6.02803349e-01,  6.61479831e-01,  4.95994329e-01,
        3.62187922e-01,  1.18813276e+00, -6.99332595e-01,  3.75821888e-01,
       -1.24131060e+00,  6.60953283e-01, -3.30733865e-01,  6.23630047e-01,
       -1.63604230e-01, -9.75265056e-02, -5.56017518e-01,  3.65739197e-01,
       -4.07576025e-01, -6.28527343e-01,  1.31811827e-01,  2.39851117e-01,
       -8.68120909e-01, -4.85356748e-01, -2.42674842e-01,  1.30489752e-01,
       -7.27526397e-02, -4.27578241e-01,  4.80079085e-01,  1.17442644e+00,
        4.61414903e-01,  1.31157711e-02,  1.78044349e-01,  5.93608916e-01,
        7.11117983e-02,  

In [27]:
sentences = sent_tokenize(article)
sentences

['Fear shakes Mexico border city after violence leaves 18 deadFear has invaded the Mexican border city of Reynosa after gunmen in vehicles killed 14 people, including taxi drivers, workers and a nursing student, and security forces responded with operations that left four suspects dead.While this city across the border from McAllen, Texas is used to cartel violence as a key trafficking point, the 14 victims in Saturday’s attacks appeared to be what Tamaulipas Gov.',
 'Francisco García Cabeza de Vaca called “innocent citizens” rather than members of one gang killed by a rival.Local businessman Misael Chavarria Garza said many businesses closed early Saturday after the attacks and people were very scared as helicopters flew overhead.',
 'On Sunday, he said, “the people were quiet as if nothing had happened, but with a feeling of anger because now crime has happened to innocent people.”“It’s not fair,” said taxi driver Rene Guevara, adding that among the dead were two of his fellow taxi d

In [28]:
sentence_embeds = []
for sent in sentences:
    embed = sbert_model.encode(sent)
    sentence_embeds.append(embed)
    
len(sentence_embeds)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

11

In [29]:
sims = []
for embed in sentence_embeds:
    sim = cosine(embed, article_embed)
    sims.append(sim)
    
len(sims)

11

In [30]:
res = pd.DataFrame()
res['Sentence'] = sentences
res['Sim Value'] = sims
res

Sentence  Sim Value
0   Fear shakes Mexico border city after violence ...   0.982563
1   Francisco García Cabeza de Vaca called “innoce...   0.795303
2   On Sunday, he said, “the people were quiet as ...   0.807429
3   Images posted on social media showed bodies in...   0.763131
4   Experts say there has been an internal struggl...   0.602479
5   Apparently, one cell from a nearby town may ha...   0.767661
6   “They stopped in front of them and started to ...   0.776007
7   He has assured Mexicans that he is fighting th...   0.622981
8   He also says he is fighting corruption to stop...   0.681011
9   “In my government, there will be no truce for ...   0.788029
10  One former governor, Tomás Yarrington, was ext...   0.596762

In [31]:
scores = sims

In [32]:
sentence_score_pairs = list(zip(sentences, scores))
sorted_pairs = sorted(sentence_score_pairs, key=lambda x: x[1], reverse=True)
top_two_pairs = sorted_pairs[:2]
top_two_sentences = [pair[0] for pair in top_two_pairs]
two_line_paragraph = '\n'.join(top_two_sentences)
print(two_line_paragraph)

Fear shakes Mexico border city after violence leaves 18 deadFear has invaded the Mexican border city of Reynosa after gunmen in vehicles killed 14 people, including taxi drivers, workers and a nursing student, and security forces responded with operations that left four suspects dead.While this city across the border from McAllen, Texas is used to cartel violence as a key trafficking point, the 14 victims in Saturday’s attacks appeared to be what Tamaulipas Gov.
On Sunday, he said, “the people were quiet as if nothing had happened, but with a feeling of anger because now crime has happened to innocent people.”“It’s not fair,” said taxi driver Rene Guevara, adding that among the dead were two of his fellow taxi drivers whom he defended and said were not involved in crime.The attacks took place in several neighborhoods in eastern Reynosa, according to the Tamaulipas state agency that coordinates security forces, and sparked a deployment of the military, National Guard and state police ac

In [33]:
summ = two_line_paragraph

In [34]:
from rouge import Rouge
rouge = Rouge()
score = rouge.get_scores(summ, df['Summary'][0], avg = True)
RougeScore = pd.DataFrame(score).set_index([['recall','precision','f-measure']])
RougeScore

rouge-1   rouge-2   rouge-l
recall     0.789474  0.772727  0.789474
precision  0.258621  0.207317  0.258621
f-measure  0.389610  0.326923  0.389610

## Finally on Dataset

In [35]:
df

Article  \
0     Fear shakes Mexico border city after violence ...   
1     Indian-origin boy finds millions of years old ...   
2     Representative ImageA 38-year-old Indian man h...   
3     Residents get tested during their stay at a te...   
4     Israeli PM Benjamin Netanyahu flew to Saudi Ar...   
...                                                 ...   
4482  FILE - Tanks storing treated radioactive water...   
4483  Villagers clear debris caused by an earthquake...   
4484  Seif al-Islam, the son and one-time heir appar...   
4485  Thai BoysMost members of the Thai youth footba...   
4486  Karachi to award citizens who identify people ...   

                                                Summary  
0     The attacks took place in several neighborhood...  
1     Siddak Singh Jhamat, known as Sid, was using a...  
2     A 38-year-old Indian man has been charged with...  
3     China on Apr 21 reported 2,119 locally transmi...  
4     Israeli media reported Monday that Prime Minis...  
...                                                 ...  
4482  A massive earthquake and tsunami in 2011 destr...  
4483  Over 680 tourists from France, Thailand, the N...  
4484  Seif al-Islam, the son and one-time heir appar...  
4485  Most members of the Thai youth football team r...  
4486  The government of Pakistan's Sindh province ha...  

[4487 rows x 2 columns]

In [36]:
pred_BERT = pd.DataFrame()
pred_BERT['Article'] = df['Article']
pred_BERT['Reference Summary'] = df['Summary']
pred_BERT

Article  \
0     Fear shakes Mexico border city after violence ...   
1     Indian-origin boy finds millions of years old ...   
2     Representative ImageA 38-year-old Indian man h...   
3     Residents get tested during their stay at a te...   
4     Israeli PM Benjamin Netanyahu flew to Saudi Ar...   
...                                                 ...   
4482  FILE - Tanks storing treated radioactive water...   
4483  Villagers clear debris caused by an earthquake...   
4484  Seif al-Islam, the son and one-time heir appar...   
4485  Thai BoysMost members of the Thai youth footba...   
4486  Karachi to award citizens who identify people ...   

                                      Reference Summary  
0     The attacks took place in several neighborhood...  
1     Siddak Singh Jhamat, known as Sid, was using a...  
2     A 38-year-old Indian man has been charged with...  
3     China on Apr 21 reported 2,119 locally transmi...  
4     Israeli media reported Monday that Prime Minis...  
...                                                 ...  
4482  A massive earthquake and tsunami in 2011 destr...  
4483  Over 680 tourists from France, Thailand, the N...  
4484  Seif al-Islam, the son and one-time heir appar...  
4485  Most members of the Thai youth football team r...  
4486  The government of Pakistan's Sindh province ha...  

[4487 rows x 2 columns]

In [ ]:
summs = []
for article in pred_BERT['Article']:
    article_embed = sbert_model.encode(article)
    sentences = sent_tokenize(article)
    sentence_embeds = []
    for sent in sentences:
        embed = sbert_model.encode(sent)
        sentence_embeds.append(embed)
    scores = []
    for embed in sentence_embeds:
        sim = cosine(embed, article_embed)
        scores.append(sim)
    sentence_score_pairs = list(zip(sentences, scores))
    sorted_pairs = sorted(sentence_score_pairs, key=lambda x: x[1], reverse=True)
    top_two_pairs = sorted_pairs[:2]
    top_two_sentences = [pair[0] for pair in top_two_pairs]
    summ = '\n'.join(top_two_sentences)
    summs.append(summ)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [39]:
pred_BERT['Generated Summary'] = summs

In [40]:
len(summs)

4487

In [41]:
pred_BERT

Article  \
0     Fear shakes Mexico border city after violence ...   
1     Indian-origin boy finds millions of years old ...   
2     Representative ImageA 38-year-old Indian man h...   
3     Residents get tested during their stay at a te...   
4     Israeli PM Benjamin Netanyahu flew to Saudi Ar...   
...                                                 ...   
4482  FILE - Tanks storing treated radioactive water...   
4483  Villagers clear debris caused by an earthquake...   
4484  Seif al-Islam, the son and one-time heir appar...   
4485  Thai BoysMost members of the Thai youth footba...   
4486  Karachi to award citizens who identify people ...   

                                      Reference Summary  \
0     The attacks took place in several neighborhood...   
1     Siddak Singh Jhamat, known as Sid, was using a...   
2     A 38-year-old Indian man has been charged with...   
3     China on Apr 21 reported 2,119 locally transmi...   
4     Israeli media reported Monday that Prime Minis...   
...                                                 ...   
4482  A massive earthquake and tsunami in 2011 destr...   
4483  Over 680 tourists from France, Thailand, the N...   
4484  Seif al-Islam, the son and one-time heir appar...   
4485  Most members of the Thai youth football team r...   
4486  The government of Pakistan's Sindh province ha...   

                                      Generated Summary  
0     Fear shakes Mexico border city after violence ...  
1     Indian-origin boy finds millions of years old ...  
2     Representative ImageA 38-year-old Indian man h...  
3     China coronavirus updates: Shanghai has extend...  
4     Israeli PM Benjamin Netanyahu flew to Saudi Ar...  
...                                                 ...  
4482  FILE - Tanks storing treated radioactive water...  
4483  At least 16 people were killed and hundreds ot...  
4484  Seif al-Islam, the son and one-time heir appar...  
4485  One of the boys will not join the ceremony as ...  
4486  Karachi to award citizens who identify people ...  

[4487 rows x 3 columns]

In [42]:
pred_BERT.to_csv("pred_bert.csv")